In [1]:
import requests
import pandas as pd

# get years that api is valid for
r_years = requests.get("https://api.dbknews.com/salary/years")
years = r_years.json()["data"]

df = pd.DataFrame()

def combine(group):
    years = group['year'].tolist()
    salaries = group['Salary'].tolist()
    salaries = [float(s.replace(",","")[1:]) for s in salaries]
    departments = group['Department'].tolist()
    
    i = 0
    while i < len(years) - 1:
        if (years[i] == years[i+1]):
            if salaries[i] != salaries[i + 1]:
                salaries[i] = salaries[i] + salaries[i + 1]
            years.pop(i+1)
            salaries.pop(i+1)
            departments.pop(i+1)
        else:
            i += 1

    return pd.Series({
        'Years Taught': years,
        'Salaries': salaries,
        'Departments': departments,
    })

for year in years:
    year_df = pd.read_csv(f'{year}data.csv')
    year_df['Employee'] = year_df['Employee'].str.replace('\n', ' ')
    df = pd.concat([df, year_df], axis=0)

df_grouped = df.groupby(['Employee']).apply(combine).reset_index()

df_grouped['Employee'] = df_grouped['Employee'].apply(lambda x: (x.split(', ')[1].split(" ")[0]+ ' ' + x.split(', ')[0].split(" ")[-1]).upper())

print(df_grouped.to_string())
df_grouped.to_csv(f'employee_data.csv', index=False)
 

                                  Employee                                                  Years Taught                                                                                                                                                              Salaries                                                   Departments
0                              EAMAN KARIM                                                  [2018, 2019]                                                                                                                                                    [48000.0, 48960.0]                                                  [ENGR, ENGR]
1                          MICHAEL A'HEARN                                [2013, 2014, 2015, 2016, 2017]                                                                                                                [125817.0, 130849.69, 145530.01, 155925.01, 135810.69]                                [CMNS, CMNS, CMNS, CMNS, CMNS]
2